## 15. Réfléchir à un autre type de réseau afin de résoudre ce problème

**=> Réseau Antagoniste Génératif (GAN)**
Les GANs sont constitués de deux réseaux : un générateur qui crée des échantillons à partir d’un bruit aléatoire et un discriminateur qui apprend à distinguer les échantillons générés de ceux réels. Pour la musique, un GAN peut générer de nouvelles séquences de notes en ajustant le générateur pour produire des séquences MIDI plausibles.

1. Architecture :
    - Le générateur utilise une séquence de bruit pour produire une séquence de notes et de durées.
    - Le discriminateur reçoit une séquence (notes et durées) et apprend à distinguer les séquences réelles (issues du dataset) des séquences générées.

2. Avantages :
    - Capte des motifs complexes grâce à l’interaction entre le générateur et le discriminateur.
    - Peut produire des séquences réalistes sans nécessiter une supervision stricte sur la structure musicale.

3. Inconvénients :
    - L'entraînement des GANs est instable et peut poser des défis pour générer des séquences de haute qualité.
    - Plus complexe pour gérer la polyphonie et les variations de tempo.


## 16. Bonus 1 : implémenter le réseau décrit à la question précédente.

In [1]:
import os
import numpy as np
import pretty_midi
import tensorflow as tf
from tensorflow.keras.layers import Dense, LSTM, Reshape, Conv1D, Flatten
from tensorflow.keras.models import Sequential
import IPython.display as ipd
import soundfile as sf

# Configuration de base
sequence_size = 100  # Nombre de notes par séquence
vocab_size = 128  # Ajusté pour couvrir la gamme de notes
latent_dim = 100  # Dimension de l'espace latent pour le générateur
batch_size = 16
epochs = 600

Cette cellule configure les paramètres de base du modèle :

- sequence_size : nombre de notes dans chaque séquence générée ou analysée.
- vocab_size : taille du vocabulaire des notes (128 est une valeur standard couvrant la gamme des notes MIDI).
- latent_dim : dimension de l'espace latent, soit la taille du vecteur de bruit en entrée du générateur pour créer de nouvelles séquences.
- batch_size : nombre de séquences traitées simultanément par le modèle.
- epochs : nombre de passages complets sur le dataset pour entraîner le modèle GAN.

Ces paramètres servent à définir les caractéristiques des séquences musicales et les réglages d'entraînement du GAN.

In [2]:

#* Charger les séquences
notes_sequences = np.load("notes_sequences.npy")
durations_sequences = np.load("durations_sequences.npy")

# Convertir les durées en entiers (discrétisation)
durations_sequences = tf.cast(durations_sequences * 100, tf.int32)  #* 100 = pas de décimales

#* Convertir en tenseurs utilisables par Tensorflow
notes_sequences = tf.convert_to_tensor(notes_sequences, dtype=tf.int32)
durations_sequences = tf.convert_to_tensor(durations_sequences, dtype=tf.int32)

Cette cellule charge les séquences de notes et de durées à partir de fichiers .npy enregistrés, qui contiennent les données nécessaires pour entraîner le modèle.

Ensuite, les durées sont converties en entiers en les multipliant par 100, supprimant les décimales pour simplifier le modèle (chaque durée est exprimée comme un multiple entier de 0,01).

Après cela, on convertit les séquences de notes et de durées en tenseurs entiers utilisables directement par TensorFlow, permettant leur utilisation pour l’entraînement du modèle

In [3]:
# Création des jeux d'entraînement pour le GAN
x_notes, y_notes = notes_sequences[:, :-1], notes_sequences[:, 1:] 
x_durations, y_durations = durations_sequences[:, :-1], durations_sequences[:, 1:]

Cette cellule crée les jeux d’entraînement pour le GAN :
- x_notes et y_notes sont créés en décalant les séquences de notes :
  - x_notes contient toutes les notes sauf la dernière de chaque séquence.
  - y_notes contient toutes les notes sauf la première de chaque séquence. Cela permet d’entraîner le modèle à prédire la note suivante à partir de la précédente.
- x_durations et y_durations suivent la même logique pour les durées, avec y_durations décalé d’un cran par rapport à x_durations, afin de prédire la durée suivante.

Ce décalage permet d’enseigner au modèle à générer progressivement une séquence musicale complète en anticipant la note et la durée suivantes.

In [4]:
# 2. Modèles de générateur et de discriminateur
    
def build_generator(latent_dim, sequence_size, vocab_size):
    model = Sequential()
    
    # Entrée
    model.add(Dense(sequence_size, activation='relu', input_dim=latent_dim))
    model.add(Reshape((sequence_size, 1)))
    
    # Couches de convolution et LSTM
    model.add(Conv1D(64, kernel_size=3, padding="same", activation="relu"))
    model.add(LSTM(128, return_sequences=True))
    
    # Branche pour les notes (avec vocab_size pour la dimension de sortie)
    notes_output = Dense(vocab_size, activation="softmax", name="notes")
    
    # Branche pour les durées (avec vocab_size pour la dimension de sortie)
    durations_output = Dense(vocab_size, activation="softmax", name="durations")
    
    # Ajout des deux branches au modèle
    model.add(notes_output)
    model.add(durations_output)
    
    return model

1. Entrée du générateur :
    - `latent_dim` est la dimension de l’espace latent (bruit aléatoire) que le générateur reçoit en entrée.
    - `input_layer` initialise cette entrée, permettant au modèle de recevoir un vecteur de taille `latent_dim`.

2. Couche dense et reshaping :
    -  `Dense` : La première couche dense transforme ce vecteur latent en une taille adaptée (`reshape_dim`) pour le traitement séquentiel, avec une activation relu qui ajoute de la non-linéarité.
    - `Reshape` : Cette sortie est ensuite transformée en une séquence de taille `sequence_size`, chaque élément étant représenté par une dimension unique.

3. Couches de convolution et LSTM :
    - `Conv1D` : Applique une convolution pour capter des motifs locaux dans la séquence, avec une activation `relu` et un noyau de taille 3.
    - `LSTM` : Utilise une couche LSTM (Long Short-Term Memory) pour capter les dépendances temporelles entre les éléments de la séquence, avec une sortie pour chaque élément (`return_sequences=True`).

4. Sorties pour les notes et durées :
    - `notes_output` : Prédit la note suivante en appliquant une couche dense avec `softmax` pour obtenir des probabilités sur toutes les notes possibles (`vocab_size`).
    - `durations_output` : Prédit la durée de chaque note de la même manière, produisant une distribution de probabilité sur toutes les durées possibles (`vocab_size`).

5. Retour du modèle :
    - Le générateur retourne un modèle prenant un vecteur latent en entrée et produisant deux sorties : une séquence de notes et une séquence de durées (`[notes_output, durations_output]`), chacune en fonction de la probabilité d'occurrence pour chaque élément dans la séquence générée.


In [5]:
def build_discriminator(sequence_size, vocab_size):
# Entrée pour les notes
    notes_input = tf.keras.Input(shape=(sequence_size, vocab_size))
    # Entrée pour les durées
    durations_input = tf.keras.Input(shape=(sequence_size, vocab_size))
    
    # Traitement des notes
    x_notes = Conv1D(64, kernel_size=3, padding="same")(notes_input)
    x_notes = LSTM(128, return_sequences=True)(x_notes)
    
    # Traitement des durées
    x_durations = Conv1D(64, kernel_size=3, padding="same")(durations_input)
    x_durations = LSTM(128, return_sequences=True)(x_durations)
    
    # Fusion des caractéristiques
    combined = tf.keras.layers.Concatenate()([x_notes, x_durations])
    x = Flatten()(combined)
    x = Dense(64, activation="relu")(x)
    output = Dense(1, activation="sigmoid")(x)
    
    return tf.keras.Model([notes_input, durations_input], output)

Ce code crée un modèle discriminateur pour un réseau GAN musical, avec deux entrées : une pour les notes et une pour les durées.

1. Entrées : notes_input et durations_input acceptent chacun des séquences (de sequence_size) avec un vocabulaire de taille vocab_size.

2. Traitement séparé :
    -  Les notes passent par une couche Conv1D pour capter des motifs locaux, suivie d'une couche LSTM pour capturer les dépendances temporelles.
    - Le même traitement est appliqué aux durées.

3. Fusion : Les sorties des deux branches sont fusionnées (Concatenate) pour combiner les caractéristiques des notes et des durées. 

4. Classification :
    - Le modèle fusionné passe par une couche Flatten, suivie d'une couche Dense avec relu pour capturer des caractéristiques globales.
    - La couche de sortie sigmoid génère une probabilité indiquant si la séquence est réelle ou générée.

Le modèle est retourné avec ses deux entrées (notes et durées) et une seule sortie binaire.

In [6]:
# 1. Compilerle discriminateur
discriminator = build_discriminator(sequence_size, vocab_size)
discriminator.compile(optimizer="adam", loss="binary_crossentropy", metrics=["accuracy"])

# 2. Compiler le générateur
generator = build_generator(latent_dim, sequence_size, vocab_size)

# 3. Compiler le GAN
def build_gan(generator, discriminator):
    discriminator.trainable = False # fixer les poids du disciminateur pendant l'entrainement du générateur
    
    gan_input = tf.keras.Input(shape=(latent_dim,))
    generated_notes, generated_durations = generator(gan_input)
    # Générer les notes avec le générateur
    gan_output = discriminator([generated_notes, generated_durations])
    
    # Créer et compiler le GAN
    gan = tf.keras.Model(gan_input, gan_output)
    gan.compile(optimizer="adam", loss="binary_crossentropy")
    return gan

gan = build_gan(generator, discriminator)

Ce code configure et compile les modèles de base pour un GAN de génération musicale, structuré autour d'un discriminateur et d'un générateur :

1. Discriminateur :
    - Le discriminateur est créé et compilé avec l'optimiseur Adam et une fonction de perte binary_crossentropy, qui est courante dans les GANs pour différencier les données générées des réelles.
    - Il retourne la précision (accuracy) pour suivre ses performances sur la classification des séquences.

2. Générateur : Le générateur est construit pour créer des séquences de notes et de durées à partir d'un vecteur de bruit de dimension latent_dim.

3. Construction du GAN :  
    - Le discriminateur est mis en mode non-entrainable (trainable = False) pour empêcher la mise à jour de ses poids lors de l’entraînement du générateur. Cela permet au GAN d’entraîner exclusivement le générateur pour améliorer ses séquences.
    - Le GAN combine le générateur et le discriminateur : il prend un vecteur de bruit, génère une séquence de notes et de durées via le générateur, puis utilise le discriminateur pour évaluer cette séquence.
    - Enfin, le GAN est compilé avec binary_crossentropy comme fonction de perte pour entraîner le générateur à tromper le discriminateur.

Le modèle GAN final est ainsi prêt à être entraîné, avec les poids du discriminateur fixés pendant cet entraînement.

In [7]:
# 3. Entraînement du GAN
# Boucle d'entraînement
for epoch in range(epochs):
    noise = np.random.normal(0, 1, (batch_size, latent_dim))
    
    generated_notes, generated_durations = generator.predict(noise)
    
    idx = tf.random.uniform([batch_size], 0, x_notes.shape[0], dtype=tf.int32)
    real_notes = tf.gather(x_notes, idx)
    real_durations = tf.gather(x_durations, idx)
    
    # One-hot encoding avec les durées converties en entiers
    real_notes = tf.one_hot(real_notes, vocab_size)
    real_durations = tf.one_hot(tf.cast(real_durations, tf.int32), vocab_size)
    
    # Entraîner le discriminateur
    discriminator.trainable = True
    d_loss_real = discriminator.train_on_batch(
        [real_notes, real_durations], 
        np.ones((batch_size, 1))
    )
    d_loss_fake = discriminator.train_on_batch(
        [generated_notes, generated_durations], 
        np.zeros((batch_size, 1))
    )
    
    # Entraîner le générateur
    discriminator.trainable = False
    g_loss = gan.train_on_batch(
        noise, 
        np.ones((batch_size, 1))
    )
    
    print(f"Epoch {epoch}, D Loss Real: {d_loss_real}, D Loss Fake: {d_loss_fake}, G Loss: {g_loss}")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 184ms/step
Epoch 0, D Loss Real: [array(0.7070498, dtype=float32), array(0.1875, dtype=float32)], D Loss Fake: [array(0.76104474, dtype=float32), array(0.09375, dtype=float32)], G Loss: [array(0.76104474, dtype=float32), array(0.76104474, dtype=float32), array(0.09375, dtype=float32)]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
Epoch 1, D Loss Real: [array(0.7115461, dtype=float32), array(0.33333334, dtype=float32)], D Loss Fake: [array(0.7018175, dtype=float32), array(0.5, dtype=float32)], G Loss: [array(0.7018175, dtype=float32), array(0.7018175, dtype=float32), array(0.5, dtype=float32)]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
Epoch 2, D Loss Real: [array(0.6486077, dtype=float32), array(0.6, dtype=float32)], D Loss Fake: [array(0.5932072, dtype=float32), array(0.6666667, dtype=float32)], G Loss: [array(0.5932072, dtype=float32), array(0.5932072, dtype=float32), array(0.6666667, dtype=float32)]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
Epoch 3, D Loss Real: [array(0.

Ce code entraîne le GAN en suivant ces étapes pour chaque époque :

1. Génération de bruit et de séquences : Un vecteur de bruit aléatoire est créé (noise), qui servira d'entrée au générateur pour produire de nouvelles séquences de notes et de durées (generated_notes et generated_durations).

2. Sélection de séquences réelles :
    - Des échantillons de séquences de notes et de durées réelles sont sélectionnés aléatoirement depuis le dataset d’entraînement (x_notes et x_durations).
    - Les notes et durées réelles sont transformées en encodage one-hot, ce qui est nécessaire pour l'entrée dans le discriminateur.

3. Entraînement du discriminateur :
    - Le discriminateur est mis en mode trainable = True.
    - Il est entraîné d’abord sur les séquences réelles (d_loss_real), avec des étiquettes de vraies données (1), puis sur les séquences générées (d_loss_fake), avec des étiquettes de fausses données (0).

4. Entraînement du générateur via le GAN :

    - Le discriminateur est temporairement mis en mode trainable = False pour entraîner uniquement le générateur.
    - Le générateur est entraîné pour "tromper" le discriminateur en passant par le modèle GAN, en générant des séquences que le discriminateur doit classer comme vraies (1), minimisant ainsi la perte du générateur (g_loss).

5. Affichage des coûts : Les coûts du discriminateur pour les séquences réelles et générées (d_loss_real, d_loss_fake) ainsi que la perte du générateur (g_loss) sont imprimées à chaque époque pour surveiller l’entraînement du GAN.


In [8]:
# Sauvegarde du générateur
generator.save("03-gan_generator.h5")

In [9]:
# 4. Génération de nouveaux morceaux
def generate_music(generator, latent_dim, num_notes=100, output_path="generated_music.mid"):
    noise = np.random.normal(0, 1, (1, latent_dim))
    generated_sequence = generator.predict(noise)
    generated_notes = tf.argmax(generated_sequence, axis=-1).numpy().flatten()

    # Création du fichier MIDI
    midi_data = pretty_midi.PrettyMIDI()
    instrument = pretty_midi.Instrument(program=0)
    current_time = 0 
    
    for pitch in generated_notes[:num_notes]:
        note = pretty_midi.Note(
            velocity=100,
            pitch=int(pitch),
            start=current_time,
            end=current_time + 0.5
        )
        instrument.notes.append(note)
        current_time += 0.5
    
    midi_data.instruments.append(instrument)
    midi_data.write(output_path)
    print(f"Morceau généré et sauvegardé sous {output_path}")

# Générer un morceau
generate_music(generator, latent_dim, num_notes=100, output_path="generated_midis/03-gan.mid")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 124ms/step
Morceau généré et sauvegardé sous generated_midis/03-gan.mid


Voici l'explication claire et concise de ce code qui génère un morceau MIDI avec le générateur du modèle GAN :

1. Création du bruit d'entrée : Un vecteur aléatoire (noise) est généré pour servir de point de départ au générateur, lui permettant de produire une séquence de notes.

2. Génération de la séquence de notes : En utilisant noise, le générateur produit une séquence probable de notes MIDI, et tf.argmax extrait l'indice de la note la plus probable pour chaque étape.

3. Construction du fichier MIDI : Un objet MIDI (midi_data) est initialisé avec un instrument (piano par défaut). Chaque note est créée avec une hauteur (pitch), une intensité (velocity), et des valeurs de début et de fin fixées à 0,5 seconde.

4. Sauvegarde du morceau : Les notes générées sont ajoutées à l'instrument, puis enregistrées dans le fichier MIDI à l'emplacement output_path. Un message confirme que le morceau a été sauvegardé.

En résumé, ce code prend un bruit aléatoire, génère une séquence MIDI avec le modèle, et enregistre cette séquence sous forme de fichier MIDI jouable.

In [10]:
output_file = "./generated_midis/03-gan.mid"
midi_data = pretty_midi.PrettyMIDI(output_file)

audio_file = "./generated_midis/03-gan.wav"
waveform = midi_data.synthesize()
sf.write(audio_file, waveform, samplerate=44100)

ipd.Audio(audio_file)